# Coletando dados de saúde suplementar da ANS
Esta rotina de coleta foi feita para usar computação distribuída em ambiente de *cloud computing*, para chegar neste objetivo, será usado:

- Databricks
- Oracle Cloud Infrastructure (OCI)

O **Databricks** permite utilizar computação distribuída gratuitamente na nuvem em sua versão *"community"*, vamos usar este ambiente para executar a rotina de coleta.

As instâncias de computação distribuída gratuitas do **Databicks** não permitem armazenamento perene dos dados, isso quer dizer que os dados que obtemos neste ambiente não podem ser armazenados por um longo prazo. Para isto, vamos transferir o resultado desta coleta para um banco de dados relacional no **OCI**.



### Dependências

Vamos instalar um [pacote desenvolvido por mim](https://pypi.org/project/ftp-download/) para superar o desafio de realizar múltiplos downloads de arquivos em servidores, e na sequência vamos instalar as demais dependências, incluindo o PySpark, que será usado aqui para transportar os dados para o banco de dados remoto.

In [0]:
!python -m pip install --upgrade -q pip
!pip install -q ftp_download
!pip freeze | grep ftp_download

ftp_download==0.1.1


In [0]:
import sys
import re
import ftp_download as ftpd
from os import path, listdir, makedirs
import logging
from ftplib import FTP
from getpass import getpass
from shutil import unpack_archive
from pyspark.dbutils import DBUtils
from pyspark.sql import SparkSession
from pyspark.sql.types import *


# sys.path.append('/dbfs/FileStore/tables/collectutils')
# import collectutils

s = SparkSession.builder.appName("dbInteract").getOrCreate()


### Variáveis de conexão com o banco de dados
Agora vamos obter as variáveis que vão nos ajudar a conectar à *"autonomous database"* que já temos alocada na Oracle.

- A `TNS_STR` é providenciada pela OCI como uma opção de conexão ao banco de dados;
- `DRIVER` é o driver de conexão que o `PySpark` vai usar para conectar com o banco de dados da Oracle;
- Vamos usar uma string de conexão `URL`, que usa informações contidas na `TNS_STR`, além do usuário `USR` e senha ` PWD` 

In [0]:
TNS_STR = "(description= (retry_count=20)(retry_delay=3)(address=(protocol=tcps)(port=1522)(host=adb.sa-saopaulo-1.oraclecloud.com))(connect_data=(service_name=g8c67f84bc4a850_demodb_high.adb.oraclecloud.com))(security=(ssl_server_dn_match=yes)))"

DRIVER = "oracle.jdbc.driver.OracleDriver"

USR = "ADMIN"
# PWD = getpass("Insira a senha de acesso do Administrador do banco de dados: ")
# URL = f"jdbc:oracle:thin:{USR}/{PWD}//adb.sa-saopaulo-1.oraclecloud.com:1522/g8c67f84bc4a850_demodb_high.adb.oraclecloud.com"
URL = f"jdbc:oracle:thin:@{TNS_STR}"


### Preparando a rotina de coleta

Nosso objetivo é conectar à um servidor FTP e baixar uma quantidade considerável de arquivos, o design da rotina abaixo leva em consideração **nossas limitações, que são**:

1. Os arquivos são `.csv` compactados dentro de arquivos `.zip`;
2. Existem dois tipos de tabelas: 
  a. *Detalhada*, e
  b. *Consolidada*, estas devem compor tabelas diferentes do nosso banco de dados;
3. Todos estes arquivos estão separados em pastas, uma para cada estado

A **estratégia adotada** consiste em:

1. Fazer múltiplos downloads concorrentes usando computação assíncrona;
2. Descompactar e organizar os arquivos localmente
3. Usar o pyspark para ler e guardar os dados no banco de dados;

In [0]:
FTP_SERVER = "ftp.dadosabertos.ans.gov.br"
ROOT_FOLDER_SRC = "/FTP/PDA/TISS/HOSPITALAR/2019/"

ftp = FTP(FTP_SERVER)
ftp.login()
remote_paths = ftp.nlst(ROOT_FOLDER_SRC)

print(remote_paths[:3])

['/FTP/PDA/TISS/HOSPITALAR/2019/AC', '/FTP/PDA/TISS/HOSPITALAR/2019/AL', '/FTP/PDA/TISS/HOSPITALAR/2019/AM']


Já sabemos que os arquivos no servidor possuem nomes regulares, eles possuem sufixo "DET" nos arquivos com a tabela detalhada, e "CONS" nas tabelas consolidadas. Sabemos também que todos os arquivos estão compactados com extensão `.zip`.

Para superar estes dois desafios, vamos criar uma função que identifica o tipo de tabela pelo nome do arquivo e extrai os conteúdos em um diretório em comum, de modo que todas as tabelas consolidadas estejam armazenadas em uma pasta, e todas as tabelas detalhadas estejam armazenadas em uma outra pasta.

In [0]:
def extract_and_organize(search_dir: str, find_patterns=["CONS", "DET"]):
    def filter_by_pattern(pattern, elements):
        matches = re.compile(pattern, re.IGNORECASE)
        return list(filter(matches.search, elements))

    filepaths = [
        f for f in listdir(search_dir) 
        if path.isfile(path.join(search_dir, f))
    ]
    listings = {i:filter_by_pattern(i, filepaths) for i in find_patterns}

    for pattern in find_patterns:
        destination = path.join(search_dir, pattern)

        if not path.exists(destination):
            makedirs(destination)

        for f in listings[pattern]:
            origin = path.join(search_dir, f)
            unpack_archive(origin, destination, "zip")

A próxima etapa vai envolver o uso de um pacote de minha autoria `ftp_download`, para saber mais sobre o projeto, visite [https://pypi.org/project/ftp-download/](https://pypi.org/project/ftp-download/). A rotina na célula abaixo segue três etapas:

1. **Download** dos arquivos para o ambiente local com `ftp_download`
2. **Descompactação e organização** dos arquivos baixados em pastas usando a rotina desenvolvida na célula anterior
3. **Movimentação dos arquivos** da unidade local para a base de dados NoSQL do databricks `dbfs`, onde o pyspark tem acesso

In [0]:
# 1
ftpd.Conf.verbose = False
# exibir log apenas com avisos e erros
ftpd.timings.log.handler.setLevel(logging.WARNING)
ftpd.timings.log.logger.setLevel(logging.WARNING)

for i, rp in enumerate(remote_paths):
    print(f"Progresso: {i/len(remote_paths)*100:.2f}%", end="\r")
    ftpd.from_folder(ftp, remote_path=rp)
print("=== Concluído! ===")

with open(ftpd.prefs.LOG_FILE) as logfile:
    logfile_contents = logfile.read()
    print(logfile_contents)

=== Concluído! ===



In [0]:
# 2
download_place = ftpd.Conf.download_folder
extract_and_organize(search_dir=download_place)

In [0]:
# 3
for subfolder in ["CONS", "DET"]:
    dbutils.fs.mv(
        f"file:{path.join(download_place, subfolder)}", 
        f"dbfs:{path.join('/ans/hosp/2019/', subfolder)}",
        recurse=True)

display(dbutils.fs.ls("dbfs:/ans/hosp/2019/"))

path name size modificationTime dbfs:/ans/hosp/2019/CONS/ CONS/ 0 0 dbfs:/ans/hosp/2019/DET/ DET/ 0 0

# Preparando a rotina de armazenamento

Agora que já temos os dados prontos para manipulação, podemos usar o `pyspark` para inserir os dados em nosso banco de dados relacional da Oracle. Para isto, vamos usar usar o [driver JDBC da Oracle](https://www.oracle.com/br/database/technologies/appdev/jdbc-downloads.html). *Esta etapa vai falhar se o driver __não__ estiver instalado no cluster atual*, para efetuar a instalação, seguimos os passos indicados [neste vídeo](https://youtu.be/3tAVXfIBqA8?si=jNeO459775ag9x44&t=261).

Vamos começar definindo um `schema` para todos os nomes de colunas possíveis. Para decidir qual o *data type* ideal para cada coluna, usamos o [dicionário de dados](https://dadosabertos.ans.gov.br/FTP/PDA/TISS/DICIONARIO/Dicionario_de_variaveis.ods) fornecido pela ANS.

In [0]:
VAR_TYPES = StructType()\
    .add("TEMPO_DE_PERMANENCIA", IntegerType(), True)\
    .add("ID_EVENTO_ATENCAO_SAUDE", IntegerType(), True)\
    .add("CD_TABELA_REFERENCIA", StringType(), True)\
    .add("CD_MUNICIPIO_BENEFICIARIO", StringType(), True)\
    .add("CD_MUNICIPIO_PRESTADOR", StringType(), True)\
    .add("UF_PRESTADOR", StringType(), True)\
    .add("CD_CARATER_ATENDIMENTO", StringType(), True)\
    .add("CD_TIPO_INTERNACAO", StringType(), True)\
    .add("CD_REGIME_INTERNACAO", StringType(), True)\
    .add("CD_MOTIVO_SAIDA", StringType(), True)\
    .add("IND_ACIDENTE_DOENCA", StringType(), True)\
    .add("ANO_MES_EVENTO", StringType(), True)\
    .add("CD_PROCEDIMENTO", StringType(), True)\
    .add("CID_1", StringType(), True)\
    .add("CID_2", StringType(), True)\
    .add("CID_3", StringType(), True)\
    .add("CID_4", StringType(), True)

Agora que temos o `schema` pronto, podemos usá-lo para ler os dados que obtemos interpretanto os tipos corretamente. Abaixo podemos ver uma amostra das tabelas consolidadas:

In [0]:
df = s.read.format("csv")\
    .option("header", True)\
    .option("delimiter", ";")\
    .option("schema", VAR_TYPES)\
    .csv("dbfs:/ans/hosp/2019/CONS/")

display(df)

ID_EVENTO_ATENCAO_SAUDE ID_PLANO FAIXA_ETARIA SEXO CD_MUNICIPIO_BENEFICIARIO PORTE CD_MODALIDADE NM_MODALIDADE CD_MUNICIPIO_PRESTADOR UF_PRESTADOR TEMPO_DE_PERMANENCIA ANO_MES_EVENTO CD_CARATER_ATENDIMENTO CD_TIPO_INTERNACAO CD_REGIME_INTERNACAO CD_MOTIVO_SAIDA CID_1 CID_2 CID_3 CID_4 QT_DIARIA_ACOMPANHANTE QT_DIARIA_UTI IND_ACIDENTE_DOENCA LG_VALOR_PREESTABELECIDO 2544679686 230439 60 a 69 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 6 2019-05 1 1 2 12 E105 null null null 0 0 9 0 2597836940 230436 80 ou mais Feminino 351490 PEQUENO 22 Cooperativa Médica 351040 SP 3 2019-05 2 1 2 12 R53 null null null 0 0 9 0 2597836930 230427 20 a 29 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 2 3 2 11 O821 null null null 0 0 9 0 2597836998 230968 5 a 9 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 2 4 2 12 R104 null null null 0 0 9 0 2597837004 230421 40 a 49 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 5 2019-05 2 2 2 12 K359 null null null 0 0 9 0 2597836927 230427 40 a 49 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 1 2 11 M870 null null null 0 0 9 0 2597836957 230427 40 a 49 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 2 2 11 M870 null null null 0 0 9 0 2597836965 230538 30 a 39 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 3 2 17 O821 null null null 0 0 9 0 2597836943 230538 30 a 39 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 3 2 17 O821 null null null 0 0 9 0 2597836990 230437 15 a 19 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 2 2 14 Q531 null null null 0 0 9 0 2597836961 230430 80 ou mais Masculino 354210 PEQUENO 22 Cooperativa Médica 351040 SP 3 2019-05 2 1 2 12 J180 null null null 0 0 9 0 2544679679 230437 1 a 4 Feminino 350950 PEQUENO 22 Cooperativa Médica 351040 SP 3 2019-05 2 4 2 12 J068 null null null 0 0 9 0 2544679684 230515 70 a 79 Masculino 354210 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 2 1 2 12 R509 null null null 0 0 9 0 2544679656 230968 1 a 4 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 2 4 2 12 J459 null null null 0 0 9 0 2597837018 230436 20 a 29 Feminino 354210 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 3 2 17 O821 null null null 0 0 9 0 2597836950 230968 60 a 69 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 3 2019-05 2 1 2 11 S335 null null null 0 0 9 0 2544679614 230427 20 a 29 Feminino 352390 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 2 2 11 S835 null null null 0 0 9 0 2544679672 230890 Não identificado null null PEQUENO 22 Cooperativa Médica 351040 SP 5 2019-05 2 1 2 12 N300 null null null 0 0 9 0 2597836956 230888 10 a 14 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 5 2019-05 2 4 2 12 L032 null null null 0 0 9 0 2597837013 230437 40 a 49 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 7 2019-05 1 1 2 12 K922 null null null 0 0 9 0 2597836942 230968 20 a 29 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 2 3 2 11 O623 null null null 0 0 9 0 2597836952 230538 30 a 39 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 3 2 17 O821 null null null 0 0 9 0 2597836921 230427 30 a 39 Masculino 351490 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 2 2 11 K409 null null null 0 0 9 0 2597836979 230437 15 a 19 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 2 1 2 11 N23 null null null 0 0 9 0 2597836999 156957 60 a 69 Masculino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 1 2 11 G561 null null null 0 0 9 0 2597836964 230437 50 a 59 Feminino 351040 PEQUENO 22 Cooperativa Médica 351040 SP 1 2019-05 1 2 2 11 N852 null null null 0 0 9 0 2597836969 230433 60 a 69 Masculino 354210 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 2 2 12 I702 null null null 0 0 9 0 2597836911 156957 30 a 39 Feminino 351490 PEQUENO 22 Cooperativa Médica 351040 SP 2 2019-05 1 3 2 17 O820 null null null 0 0 9 0 259783

ler depois
- https://docs.oracle.com/cloud/help/pt_BR/analytics-cloud/ACSDS/GUID-FB2AEC3B-2178-48DF-8B9F-76ED2D6B5194.htm#ACSDS-GUID-FB2AEC3B-2178-48DF-8B9F-76ED2D6B5194
- https://docs.oracle.com/en-us/iaas/autonomous-database-serverless/doc/connect-jdbc-thin-wallet.html#GUID-BE543CFD-6FB4-4C5B-A2EA-9638EC30900D

In [0]:
drivername = "oracle.jdbc.OracleDriver"
# tablename = "hosp_cons_2019"
tablename = "test_table"
URL = "jdbc:oracle:thin:@dbname_high?TNS_ADMIN=/home/vflins/lib/Wallet_demodb"
df.write.format("jdbc")\
	.option("driver", drivername)\
	.option("url", URL)\
	.option("dbtable", tablename )\
	.option("user", USR)\
	.option("password", PWD)\
	.save()

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-1973142381364460>:9
      1 drivername = "oracle.jdbc.OracleDriver"
      2 tablename = "hosp_cons_2019"
      4 df.write.format("jdbc")\
      5 	.option("driver", drivername)\
      6 	.option("url", URL)\
      7 	.option("dbtable", tablename )\
      8 	.option("user", USR)\
----> 9 	.option("password", PWD)\
     10 	.save()

NameError: name 'PWD' is not defined

In [0]:
!sudo apt-get -qq install default-jre -y
!sudo apt-get -qq install default-jdk -y
!java -version




The following additional packages will be installed:
  ca-certificates-java default-jre-headless fonts-dejavu-extra
  libatk-wrapper-java libatk-wrapper-java-jni libpcsclite1 openjdk-11-jre
  openjdk-11-jre-headless
Suggested packages:
  pcscd libnss-mdns fonts-ipafont-gothic fonts-ipafont-mincho
  fonts-wqy-microhei | fonts-wqy-zenhei fonts-indic
The following NEW packages will be installed:
  ca-certificates-java default-jre default-jre-headless fonts-dejavu-extra
  libatk-wrapper-java libatk-wrapper-java-jni libpcsclite1 openjdk-11-jre
  openjdk-11-jre-headless
0 upgraded, 9 newly installed, 0 to remove and 12 not upgraded.
Need to get 40.5 MB of archives.
After this operation, 184 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu focal/main amd64 libpcsclite1 amd64 1.8.26-3 [22.0 kB]
Ign:2 http://archive.ubuntu.com/ubuntu focal-updates/main amd64 openjdk-11-jre-headless amd64 11.0.21+9-0ubuntu1~20.04
Get:3 http://archive.ubuntu.com/ubuntu focal/mai

In [0]:
df = s.read.format("csv")\
    .option("header", True)\
    .option("delimiter", ";")\
    .option("schema", VAR_TYPES)\
    .csv("dbfs:/ans/hosp/2019/DET/")

display(df)

In [0]:
drivername = "oracle.jdbc.OracleDriver"
tablename = "hosp_det_2019"

df.write.format("jdbc")\
	.option("driver", drivername)\
	.option("url", URL)\
	.option("dbtable", tablename )\
	.option("user", USR)\
	.option("password", PWD)\
	.save()